In [1]:
from glob import glob
import os

dataset_root = "./"
label_files = glob(os.path.join(dataset_root, "**", "*.txt"), recursive=True)

class_counts = {}

for label_file in label_files:
    with open(label_file) as f:
        for line_num, line in enumerate(f, start=1):
            line = line.strip()
            if not line or line.startswith('#'):
                continue
            parts = line.split()
            if not parts[0].isdigit():
                print(f"Skipping line in {label_file}, line {line_num}: {line}")
                continue
            class_id = int(parts[0])
            class_counts[class_id] = class_counts.get(class_id, 0) + 1

print("\nClass distribution after cleanup:")
for class_id in sorted(class_counts):
    print(f"Class {class_id}: {class_counts[class_id]} instances")


Skipping line in .\README.dataset.txt, line 2: https://universe.roboflow.com/celldetection-ok5sm/dental-x-ray-panoramic-dataset
Skipping line in .\README.dataset.txt, line 4: Provided by a Roboflow user
Skipping line in .\README.dataset.txt, line 5: License: CC BY 4.0
Skipping line in .\README.roboflow.txt, line 2: Dental X-Ray Panoramic Dataset - v2 2025-02-06 4:50pm
Skipping line in .\README.roboflow.txt, line 3: ==============================
Skipping line in .\README.roboflow.txt, line 5: This dataset was exported via roboflow.com on February 25, 2025 at 9:44 AM GMT
Skipping line in .\README.roboflow.txt, line 7: Roboflow is an end-to-end computer vision platform that helps you
Skipping line in .\README.roboflow.txt, line 8: * collaborate with your team on computer vision projects
Skipping line in .\README.roboflow.txt, line 9: * collect & organize images
Skipping line in .\README.roboflow.txt, line 10: * understand and search unstructured image data
Skipping line in .\README.robof

In [2]:
import os
from glob import glob

# === Setup ===
dataset_root = "./"  # or your dataset path
keep_classes = {
    0: 0,    # Bone Loss
    1: 1,    # Caries
    2: 2,    # Crown
    4: 3,    # Filling
    6: 4,    # Implant
    8: 5,    # Mandibular Canal
    9: 6,    # Missing teeth
    10: 7,   # Periapical lesion
    14: 8,   # Root Canal Treatment
    15: 9,   # Root Piece
    20: 10,  # attrition
    23: 11   # impacted tooth
}

# === Scan All YOLO Label Files ===
label_files = glob(os.path.join(dataset_root, "**", "labels", "*.txt"), recursive=True)

for label_path in label_files:
    with open(label_path, 'r') as f:
        lines = f.readlines()

    new_lines = []
    for line in lines:
        line = line.strip()
        if not line or not line[0].isdigit():
            continue
        parts = line.split()
        old_id = int(parts[0])
        if old_id in keep_classes:
            parts[0] = str(keep_classes[old_id])
            new_lines.append(" ".join(parts) + "\n")

    # Overwrite or delete file
    if new_lines:
        with open(label_path, 'w') as f:
            f.writelines(new_lines)
    else:
        # No valid annotations → delete label + image
        os.remove(label_path)
        image_name = os.path.splitext(os.path.basename(label_path))[0]
        image_dir = label_path.replace("labels", "images").rsplit('/', 1)[0]
        for ext in ['.jpg', '.png', '.jpeg']:
            img_path = os.path.join(image_dir, image_name + ext)
            if os.path.exists(img_path):
                os.remove(img_path)
                break


In [3]:
from glob import glob
import os

dataset_root = "./"
label_files = glob(os.path.join(dataset_root, "**", "*.txt"), recursive=True)

class_counts = {}

for label_file in label_files:
    with open(label_file) as f:
        for line_num, line in enumerate(f, start=1):
            line = line.strip()
            if not line or line.startswith('#'):
                continue
            parts = line.split()
            if not parts[0].isdigit():
                print(f"Skipping line in {label_file}, line {line_num}: {line}")
                continue
            class_id = int(parts[0])
            class_counts[class_id] = class_counts.get(class_id, 0) + 1

print("\nClass distribution after cleanup:")
for class_id in sorted(class_counts):
    print(f"Class {class_id}: {class_counts[class_id]} instances")


Skipping line in .\README.dataset.txt, line 2: https://universe.roboflow.com/celldetection-ok5sm/dental-x-ray-panoramic-dataset
Skipping line in .\README.dataset.txt, line 4: Provided by a Roboflow user
Skipping line in .\README.dataset.txt, line 5: License: CC BY 4.0
Skipping line in .\README.roboflow.txt, line 2: Dental X-Ray Panoramic Dataset - v2 2025-02-06 4:50pm
Skipping line in .\README.roboflow.txt, line 3: ==============================
Skipping line in .\README.roboflow.txt, line 5: This dataset was exported via roboflow.com on February 25, 2025 at 9:44 AM GMT
Skipping line in .\README.roboflow.txt, line 7: Roboflow is an end-to-end computer vision platform that helps you
Skipping line in .\README.roboflow.txt, line 8: * collaborate with your team on computer vision projects
Skipping line in .\README.roboflow.txt, line 9: * collect & organize images
Skipping line in .\README.roboflow.txt, line 10: * understand and search unstructured image data
Skipping line in .\README.robof

In [4]:
import os
import shutil

# Correct class remapping: {source_class_id: target_class_id}
class_remap = {
    6: 4,    # Implant
    15: 9,   # Root Piece
    10: 6,   # Missing Teeth
    11: 7,   # Periapical Lesion
    0: 0     # Bone Loss
}

# === CONFIG: Source and Target Directories ===
source_root = "../dental-x-ray-panoramic.v2i.yolov8 (2)"  # ← Change to the correct folder
target_root = "./"  # This is your current YOLO base dataset root

splits = ["train", "valid", "test"]

def safe_merge(s):
    src_label_dir = os.path.join(source_root, s, "labels")
    src_img_dir = os.path.join(source_root, s, "images")

    dst_label_dir = os.path.join(target_root, s, "labels")
    dst_img_dir = os.path.join(target_root, s, "images")

    os.makedirs(dst_label_dir, exist_ok=True)
    os.makedirs(dst_img_dir, exist_ok=True)

    merged = 0
    skipped = 0
    already_exists = 0

    for fname in os.listdir(src_label_dir):
        if not fname.endswith(".txt"):
            continue

        label_path = os.path.join(src_label_dir, fname)
        with open(label_path, "r") as f:
            lines = f.readlines()

        # Remap and filter only desired classes
        new_lines = []
        for line in lines:
            parts = line.strip().split()
            class_id = int(parts[0])
            if class_id in class_remap:
                parts[0] = str(class_remap[class_id])
                new_lines.append(" ".join(parts) + "\n")

        if not new_lines:
            skipped += 1
            continue

        # Check if corresponding image exists
        base = os.path.splitext(fname)[0]
        img_found = False
        for ext in [".jpg", ".jpeg", ".png"]:
            src_img_path = os.path.join(src_img_dir, base + ext)
            if os.path.exists(src_img_path):
                dst_img_path = os.path.join(dst_img_dir, os.path.basename(src_img_path))
                dst_label_path = os.path.join(dst_label_dir, fname)

                # Skip if image already in base
                if os.path.exists(dst_img_path):
                    already_exists += 1
                    break

                # Copy image and label
                shutil.copy(src_img_path, dst_img_path)
                with open(dst_label_path, "w") as f_out:
                    f_out.writelines(new_lines)

                merged += 1
                img_found = True
                break

        if not img_found:
            skipped += 1

    print(f"📂 Split: {s}")
    print(f"✅ Merged: {merged} files")
    print(f"⚠️ Skipped (no target class or image): {skipped}")
    print(f"⛔ Already existed in base: {already_exists}")
    print()

# === Run merge for all splits ===
for split in splits:
    safe_merge(split)


📂 Split: train
✅ Merged: 3007 files
⚠️ Skipped (no target class or image): 6570
⛔ Already existed in base: 0

📂 Split: valid
✅ Merged: 875 files
⚠️ Skipped (no target class or image): 1864
⛔ Already existed in base: 0

📂 Split: test
✅ Merged: 421 files
⚠️ Skipped (no target class or image): 948
⛔ Already existed in base: 0



In [5]:
from collections import Counter
from pathlib import Path

label_dirs = ['train/labels', 'valid/labels', 'test/labels']  # Adjust if your structure is different
class_counter = Counter()

for label_dir in label_dirs:
    for label_file in Path(label_dir).rglob('*.txt'):
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if parts:  # skip empty lines
                    class_id = int(parts[0])
                    class_counter[class_id] += 1

print("📊 Final Class Distribution:")
for cls_id in sorted(class_counter):
    print(f"Class {cls_id}: {class_counter[cls_id]} instances")


📊 Final Class Distribution:
Class 0: 6204 instances
Class 1: 10592 instances
Class 2: 11155 instances
Class 3: 48694 instances
Class 4: 3533 instances
Class 5: 619 instances
Class 6: 8645 instances
Class 7: 5227 instances
Class 8: 18887 instances
Class 9: 5187 instances
Class 10: 44 instances
Class 11: 27872 instances


In [2]:
import os
import shutil

# YOLO source path
YOLO_PATH = "../../YOLO/train"

# Your base dataset's existing path
BASE_PATH = "../base2/train"

# Class ID mapping from YOLO → Base
class_map = {
    13: 0,   # Bone_loss
    3: 4,    # Implant
    7: 7,    # Periapical lesion
    10: 9    # Root_piece
}

# Make sure base folders exist
os.makedirs(os.path.join(BASE_PATH, "labels"), exist_ok=True)
os.makedirs(os.path.join(BASE_PATH, "images"), exist_ok=True)

added_count = 0
skipped = 0

for label_file in os.listdir(os.path.join(YOLO_PATH, "labels")):
    label_path = os.path.join(YOLO_PATH, "labels", label_file)
    with open(label_path, 'r') as f:
        lines = f.readlines()

    new_lines = []
    for line in lines:
        parts = line.strip().split()
        if not parts:
            continue
        class_id = int(parts[0])
        if class_id in class_map:
            parts[0] = str(class_map[class_id])
            new_lines.append(" ".join(parts))

    if new_lines:
        # Target file paths
        target_label = os.path.join(BASE_PATH, "labels", label_file)
        target_image = os.path.join(BASE_PATH, "images", label_file.replace(".txt", ".jpg"))

        # Avoid duplicates
        if os.path.exists(target_label):
            skipped += 1
            continue

        # Write new label file
        with open(target_label, 'w') as f:
            f.write("\n".join(new_lines))

        # Copy image (.jpg or .png)
        src_img = os.path.join(YOLO_PATH, "images", label_file.replace(".txt", ".jpg"))
        if not os.path.exists(src_img):
            src_img = os.path.join(YOLO_PATH, "images", label_file.replace(".txt", ".png"))

        if os.path.exists(src_img):
            shutil.copy(src_img, target_image)
            added_count += 1
        else:
            print(f"⚠️ Image not found for: {label_file}")

print(f"✅ Done! Added {added_count} files. Skipped {skipped} duplicates.")


✅ Done! Added 2912 files. Skipped 0 duplicates.


In [3]:
from collections import Counter
from pathlib import Path

label_dirs = ['train/labels', 'valid/labels', 'test/labels']  # Adjust if your structure is different
class_counter = Counter()

for label_dir in label_dirs:
    for label_file in Path(label_dir).rglob('*.txt'):
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if parts:  # skip empty lines
                    class_id = int(parts[0])
                    class_counter[class_id] += 1

print("📊 Final Class Distribution:")
for cls_id in sorted(class_counter):
    print(f"Class {cls_id}: {class_counter[cls_id]} instances")

📊 Final Class Distribution:
Class 0: 8850 instances
Class 1: 10592 instances
Class 2: 11155 instances
Class 3: 48694 instances
Class 4: 4761 instances
Class 5: 619 instances
Class 6: 8645 instances
Class 7: 8083 instances
Class 8: 18887 instances
Class 9: 6913 instances
Class 10: 44 instances
Class 11: 27872 instances


In [4]:
import os
from tqdm import tqdm

# Define the paths to your label directories
label_dirs = [
    "./train/labels",
    "./valid/labels",
    "./test/labels"
]

# IDs of dropped classes
invalid_ids = {"5", "10"}
deleted_files = 0
updated_files = 0

for label_dir in label_dirs:
    for file in tqdm(os.listdir(label_dir), desc=f"Scanning {label_dir}"):
        if not file.endswith(".txt"):
            continue
        path = os.path.join(label_dir, file)
        
        with open(path, "r") as f:
            lines = f.readlines()

        new_lines = [line for line in lines if line.split()[0] not in invalid_ids]

        if len(new_lines) == 0:
            os.remove(path)
            deleted_files += 1
        elif len(new_lines) != len(lines):
            with open(path, "w") as f:
                f.writelines(new_lines)
            updated_files += 1

print(f"✅ Cleanup complete.")
print(f"🗑️ Label files deleted (only invalid classes): {deleted_files}")
print(f"✏️ Label files updated (partial removal): {updated_files}")


Scanning ./test/labels: 100%|██████████| 1800/1800 [00:00<00:00, 3984.14it/s]

✅ Cleanup complete.
🗑️ Label files deleted (only invalid classes): 20
✏️ Label files updated (partial removal): 315


In [7]:
from collections import Counter
from pathlib import Path

label_dirs = ['train/labels', 'valid/labels', 'test/labels']  # Adjust if your structure is different
class_counter = Counter()

for label_dir in label_dirs:
    for label_file in Path(label_dir).rglob('*.txt'):
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if parts:  # skip empty lines
                    class_id = int(parts[0])
                    class_counter[class_id] += 1

print("📊 Final Class Distribution:")
for cls_id in sorted(class_counter):
    print(f"Class {cls_id}: {class_counter[cls_id]} instances")

📊 Final Class Distribution:
Class 0: 8850 instances
Class 1: 10592 instances
Class 2: 11155 instances
Class 3: 48694 instances
Class 4: 4761 instances
Class 5: 8645 instances
Class 6: 8083 instances
Class 7: 18887 instances
Class 8: 6913 instances
Class 9: 27872 instances


In [6]:
import os
from tqdm import tqdm

# Old → New class ID mapping
id_map = {
    "0": "0",
    "1": "1",
    "2": "2",
    "3": "3",
    "4": "4",
    "6": "5",
    "7": "6",
    "8": "7",
    "9": "8",
    "11": "9"
}

label_dirs = [
    "./train/labels",
    "./valid/labels",
    "./test/labels"
]

for label_dir in label_dirs:
    for file in tqdm(os.listdir(label_dir), desc=f"Remapping in {label_dir}"):
        if not file.endswith(".txt"):
            continue
        path = os.path.join(label_dir, file)
        with open(path, "r") as f:
            lines = f.readlines()
        
        new_lines = []
        for line in lines:
            parts = line.strip().split()
            if parts[0] in id_map:
                parts[0] = id_map[parts[0]]
                new_lines.append(" ".join(parts) + "\n")
        
        with open(path, "w") as f:
            f.writelines(new_lines)

print("✅ Remapping complete. All label files are updated.")


Remapping in ./test/labels: 100%|██████████| 1797/1797 [00:03<00:00, 450.68it/s]

✅ Remapping complete. All label files are updated.


In [8]:
import albumentations as A
import cv2
import os
from glob import glob
from tqdm import tqdm

# ⚙️ CONFIGURATION
DATASET_DIR = './train'  # only augment training data
IMAGE_DIR = os.path.join(DATASET_DIR, 'images')
LABEL_DIR = os.path.join(DATASET_DIR, 'labels')
AUG_PER_IMAGE = 3
TARGET_CLASSES = [4, 9]  # underrepresented classes

# 📦 Augmentation pipeline
augment = A.Compose([
    A.HorizontalFlip(p=0.5),
    A.RandomBrightnessContrast(p=0.5),
    A.Rotate(limit=15, p=0.5),
    A.RandomScale(scale_limit=0.2, p=0.5),
    A.ShiftScaleRotate(shift_limit=0.1, scale_limit=0.1, rotate_limit=20, p=0.5),
    A.Blur(p=0.2),
    A.GaussNoise(p=0.2),
], bbox_params=A.BboxParams(format='yolo', label_fields=['class_labels']))

# 🚀 Augment images with low-class labels
label_files = glob(os.path.join(LABEL_DIR, '*.txt'))

for label_path in tqdm(label_files, desc='Augmenting low-frequency class images'):
    base_filename = os.path.basename(label_path).replace('.txt', '')
    image_path = os.path.join(IMAGE_DIR, base_filename + '.jpg')
    if not os.path.exists(image_path):
        image_path = os.path.join(IMAGE_DIR, base_filename + '.png')
        if not os.path.exists(image_path):
            continue

    # Load image
    image = cv2.imread(image_path)
    if image is None:
        continue
    h, w = image.shape[:2]

    # Load YOLO label
    with open(label_path, 'r') as f:
        lines = f.readlines()

    bboxes = []
    class_labels = []
    has_target_class = False

    for line in lines:
        parts = line.strip().split()
        cls = int(parts[0])
        bbox = list(map(float, parts[1:]))
        bboxes.append(bbox)
        class_labels.append(cls)
        if cls in TARGET_CLASSES:
            has_target_class = True

    if not has_target_class:
        continue  # Skip images with no target class

    # Apply augmentations
    for i in range(AUG_PER_IMAGE):
        try:
            augmented = augment(image=image, bboxes=bboxes, class_labels=class_labels)
            aug_img = augmented['image']
            aug_bboxes = augmented['bboxes']
            aug_classes = augmented['class_labels']

            # Save augmented image
            aug_img_name = f"{base_filename}_aug{i}.jpg"
            aug_img_path = os.path.join(IMAGE_DIR, aug_img_name)
            aug_lbl_path = os.path.join(LABEL_DIR, aug_img_name.replace('.jpg', '.txt'))

            cv2.imwrite(aug_img_path, aug_img)

            # Save augmented label
            with open(aug_lbl_path, 'w') as f:
                for cls, bbox in zip(aug_classes, aug_bboxes):
                    f.write(f"{cls} {' '.join(map(str, bbox))}\n")

        except Exception as e:
            print(f"Skipping {base_filename} augmentation due to: {e}")


C:\Users\User\AppData\Roaming\Python\Python312\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
C:\Users\User\AppData\Roaming\Python\Python312\site-packages\albumentations\core\validation.py:114: UserWarning: ShiftScaleRotate is a special case of Affine transform. Please use Affine transform instead.
  original_init(self, **validated_kwargs)
Augmenting low-frequency class images:   0%|          | 41/15577 [00:00<04:49, 53.72it/s]

Skipping 026e78e8-GHASEMI_MASOMEH_2020-06-15134512_jpg.rf.2dc9752aaaa6977f10a8d96b72ab3234 augmentation due to: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (5,) + inhomogeneous part.
Skipping 026e78e8-GHASEMI_MASOMEH_2020-06-15134512_jpg.rf.2dc9752aaaa6977f10a8d96b72ab3234 augmentation due to: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (5,) + inhomogeneous part.
Skipping 026e78e8-GHASEMI_MASOMEH_2020-06-15134512_jpg.rf.2dc9752aaaa6977f10a8d96b72ab3234 augmentation due to: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (5,) + inhomogeneous part.
Skipping 026e78e8-GHASEMI_MASOMEH_2020-06-15134512_jpg.rf.393408c183ac283f88dd529eaf92798b augmentation due to: Expected y_max for bbox [0.18550348 0.4161233  0.60753655 1.2630394  0.4381

Augmenting low-frequency class images:   0%|          | 72/15577 [00:01<04:28, 57.66it/s]

Skipping 045c8267-Hoseyni_Mehrshad_41yo_01062021_150420_jpg.rf.12bbcd78a5b6a2428427ca7bf9836409 augmentation due to: Expected x_max for bbox [0.36496776 0.18452261 1.0023835  0.56679994 0.65087754 0.476398
 0.6971374  0.469782   0.68367565 0.37566128 2.        ] to be in the range [0.0, 1.0], got 1.0023834705352783.
Skipping 045c8267-Hoseyni_Mehrshad_41yo_01062021_150420_jpg.rf.12bbcd78a5b6a2428427ca7bf9836409 augmentation due to: Expected x_max for bbox [0.36496776 0.18452261 1.0023835  0.56679994 0.65087754 0.476398
 0.6971374  0.469782   0.68367565 0.37566128 2.        ] to be in the range [0.0, 1.0], got 1.0023834705352783.
Skipping 045c8267-Hoseyni_Mehrshad_41yo_01062021_150420_jpg.rf.12bbcd78a5b6a2428427ca7bf9836409 augmentation due to: Expected x_max for bbox [0.36496776 0.18452261 1.0023835  0.56679994 0.65087754 0.476398
 0.6971374  0.469782   0.68367565 0.37566128 2.        ] to be in the range [0.0, 1.0], got 1.0023834705352783.
Skipping 045c8267-Hoseyni_Mehrshad_41yo_010620

Augmenting low-frequency class images:   1%|          | 84/15577 [00:01<04:52, 53.02it/s]

...

Augmenting low-frequency class images: 100%|█████████▉| 15515/15577 [08:43<00:01, 45.47it/s]

Skipping fac5d408-Abbasi_vardeh_Hossein_2022-06-12141910_jpg.rf.e7f18a7f3eb3d56e5d620387335a2639 augmentation due to: Expected x_max for bbox [0.32903424 0.29564324 1.0011483  0.8874761  0.6735553  0.5547842
 0.6665326  0.554511   0.6650913  0.59155965 3.        ] to be in the range [0.0, 1.0], got 1.0011483430862427.
Skipping fac5d408-Abbasi_vardeh_Hossein_2022-06-12141910_jpg.rf.e7f18a7f3eb3d56e5d620387335a2639 augmentation due to: Expected x_max for bbox [0.32903424 0.29564324 1.0011483  0.8874761  0.6735553  0.5547842
 0.6665326  0.554511   0.6650913  0.59155965 3.        ] to be in the range [0.0, 1.0], got 1.0011483430862427.
Skipping fac5d408-Abbasi_vardeh_Hossein_2022-06-12141910_jpg.rf.e7f18a7f3eb3d56e5d620387335a2639 augmentation due to: Expected x_max for bbox [0.32903424 0.29564324 1.0011483  0.8874761  0.6735553  0.5547842
 0.6665326  0.554511   0.6650913  0.59155965 3.        ] to be in the range [0.0, 1.0], got 1.0011483430862427.


Augmenting low-frequency class images: 100%|█████████▉| 15533/15577 [08:44<00:00, 46.26it/s]

Skipping fc3ca101-Mohamadi_Fatemeh_2022-05-14192255_jpg.rf.653c3d697537e814cece730cae868558 augmentation due to: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (12,) + inhomogeneous part.
Skipping fc3ca101-Mohamadi_Fatemeh_2022-05-14192255_jpg.rf.653c3d697537e814cece730cae868558 augmentation due to: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (12,) + inhomogeneous part.
Skipping fc3ca101-Mohamadi_Fatemeh_2022-05-14192255_jpg.rf.653c3d697537e814cece730cae868558 augmentation due to: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (12,) + inhomogeneous part.
Skipping fc3ca101-Mohamadi_Fatemeh_2022-05-14192255_jpg.rf.d28883c389f563270afb329eb8a12912 augmentation due to: Expected y_max for bbox [0.17428912 0.3562882  0.5095891  1.0649507 

Augmenting low-frequency class images: 100%|██████████| 15577/15577 [08:45<00:00, 29.67it/s]


In [1]:
from collections import Counter
from pathlib import Path

label_dirs = ['./data/test/labels', './data/train/labels', './data/valid/labels']  # Adjust if your structure is different
class_counter = Counter()

for label_dir in label_dirs:
    for label_file in Path(label_dir).rglob('*.txt'):
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if parts:  # skip empty lines
                    class_id = int(float(parts[0])) 
                    class_counter[class_id] += 1

print("📊 Final Class Distribution:")
for cls_id in sorted(class_counter):
    print(f"Class {cls_id}: {class_counter[cls_id]} instances")

📊 Final Class Distribution:
Class 0: 8850 instances
Class 1: 10667 instances
Class 2: 11404 instances
Class 3: 34641 instances
Class 4: 5880 instances
Class 5: 8720 instances
Class 6: 8116 instances
Class 7: 19151 instances
Class 8: 6958 instances
Class 9: 28682 instances


In [11]:
import os
from glob import glob
from tqdm import tqdm

# ✅ Configuration
LABEL_DIR = './train/labels'  # 🔁 Change this to your actual path
TARGET_CLASS_ID = 3
TARGET_COUNT = 20000
current_count = 0

# Step 1: Get all label files
label_files = sorted(glob(os.path.join(LABEL_DIR, '*.txt')))
print(f"Found {len(label_files)} label files.")

# Step 2: Walk through and safely trim class 3
for label_path in tqdm(label_files, desc="Trimming class 3 instances"):
    with open(label_path, 'r') as f:
        lines = [line.strip() for line in f if line.strip()]

    new_lines = []
    for line in lines:
        class_id = int(float(line.split()[0]))
        if class_id == TARGET_CLASS_ID:
            if current_count < TARGET_COUNT:
                new_lines.append(line)
                current_count += 1
            else:
                continue  # Skip extra class 3 instances
        else:
            new_lines.append(line)  # Keep other classes

    # Save modified label file
    with open(label_path, 'w') as f:
        for l in new_lines:
            f.write(l + '\n')

print(f"\n✅ Done. Final class 3 count kept: {current_count} lines.")


Found 16990 label files.


Trimming class 3 instances: 100%|██████████| 16990/16990 [00:35<00:00, 484.29it/s]


✅ Done. Final class 3 count kept: 20000 lines.


In [ ]:
import os
import cv2
import numpy as np
import albumentations as A
import random
from collections import defaultdict

# Configuration
IMAGE_DIR = "./data/train/images"
LABEL_DIR = "./data/train/labels"

# Target classes and how many more instances to generate
AUGMENT_CLASSES = {
    4: 3120,
    6: 1384,
    8: 2042
}

# Albumentations transform
transform = A.Compose([
    A.HorizontalFlip(p=0.5),
    A.RandomBrightnessContrast(p=0.3),
    A.ShiftScaleRotate(shift_limit=0.05, scale_limit=0.1, rotate_limit=10, p=0.5),
    A.GaussianBlur(p=0.2)
], bbox_params=A.BboxParams(format='yolo', label_fields=['class_labels'], min_visibility=0.3))

def clip_bbox(bbox):
    x, y, w, h = bbox[:4]
    x = np.clip(x, 0, 1)
    y = np.clip(y, 0, 1)
    w = np.clip(w, 0, 1)
    h = np.clip(h, 0, 1)
    return [x, y, w, h, bbox[4]]

def load_image_and_labels(image_path, label_path):
    image = cv2.imread(image_path)
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    bboxes = []
    class_labels = []
    with open(label_path, 'r') as f:
        for line in f:
            parts = line.strip().split()
            if len(parts) != 5:
                continue
            cls, x, y, w, h = map(float, parts)
            bboxes.append([x, y, w, h, cls])
            class_labels.append(int(cls))
    return image, bboxes, class_labels

def augment_class_images():
    image_files = os.listdir(IMAGE_DIR)
    class_to_images = defaultdict(list)

    # Group images that include target classes
    for img_file in image_files:
        label_file = img_file.rsplit(".", 1)[0] + ".txt"
        label_path = os.path.join(LABEL_DIR, label_file)
        if not os.path.exists(label_path):
            continue
        with open(label_path, 'r') as f:
            lines = f.readlines()
        for line in lines:
            cls_id = int(float(line.strip().split()[0]))
            if cls_id in AUGMENT_CLASSES:
                class_to_images[cls_id].append((img_file, label_file))
                break  # avoid duplicates

    # Start augmentation
    for cls_id, target_count in AUGMENT_CLASSES.items():
        print(f"🔄 Augmenting class {cls_id} to add {target_count} samples")
        images = class_to_images[cls_id]
        i = 0
        while i < target_count:
            img_name, lbl_name = random.choice(images)
            img_path = os.path.join(IMAGE_DIR, img_name)
            lbl_path = os.path.join(LABEL_DIR, lbl_name)
            image, bboxes, labels = load_image_and_labels(img_path, lbl_path)

            # Filter only target class
            filtered = [(b, l) for b, l in zip(bboxes, labels) if l == cls_id]
            if not filtered:
                continue

            f_bboxes, f_labels = zip(*filtered)
            clipped_bboxes = [clip_bbox(b) for b in f_bboxes]

            try:
                aug = transform(image=image, bboxes=clipped_bboxes, class_labels=list(f_labels))
                aug_img = aug['image']
                aug_bboxes = aug['bboxes']
                aug_labels = aug['class_labels']

                # Unique name
                aug_filename = f"cls{cls_id}_aug_{i}.jpg"
                aug_txt = aug_filename.replace(".jpg", ".txt")

                # Save image
                cv2.imwrite(os.path.join(IMAGE_DIR, aug_filename), cv2.cvtColor(aug_img, cv2.COLOR_RGB2BGR))

                # Save label
                with open(os.path.join(LABEL_DIR, aug_txt), 'w') as f:
                    for bbox, label in zip(aug_bboxes, aug_labels):
                        f.write(f"{label} {' '.join(map(str, bbox[:4]))}\n")

                i += 1
            except Exception as e:
                print(f"⚠️ Skipped one due to: {e}")

augment_class_images()
print("✅ Done: Augmented files saved directly into YOLO folder.")
           

C:\Users\User\AppData\Roaming\Python\Python312\site-packages\albumentations\core\validation.py:114: UserWarning: ShiftScaleRotate is a special case of Affine transform. Please use Affine transform instead.
  original_init(self, **validated_kwargs)


🔄 Augmenting class 4 to add 3120 samples


In [1]:
from collections import Counter
from pathlib import Path

label_dirs = ['./data/test/labels', './data/train/labels', './data/valid/labels']  # Adjust if your structure is different
class_counter = Counter()

for label_dir in label_dirs:
    for label_file in Path(label_dir).rglob('*.txt'):
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if parts:  # skip empty lines
                    class_id = int(float(parts[0])) 
                    class_counter[class_id] += 1

print("📊 Final Class Distribution:")
for cls_id in sorted(class_counter):
    print(f"Class {cls_id}: {class_counter[cls_id]} instances")

📊 Final Class Distribution:
Class 0: 8850 instances
Class 1: 10667 instances
Class 2: 11404 instances
Class 3: 34641 instances
Class 4: 5880 instances
Class 5: 8720 instances
Class 6: 8116 instances
Class 7: 19151 instances
Class 8: 6958 instances
Class 9: 28682 instances


## DownSample to make dataset balanced
## Class 3: 34,641 → 12,000
## Class 9: 28,682 → 12,000
## Class 7: 19,151 → 12,000

In [13]:
import os
import random
from collections import defaultdict

# 📁 Paths
label_dir = "./data/train/labels"

# ⚙️ Configuration
target_classes = [3, 7, 9]
max_instances = 12000

# 🧮 Step 1: Count bounding boxes per class and store their file locations
bbox_pool = defaultdict(list)  # {class_id: [(file_path, line_index), ...]}

for label_file in os.listdir(label_dir):
    if not label_file.endswith(".txt"):
        continue
    full_path = os.path.join(label_dir, label_file)
    with open(full_path, "r") as f:
        lines = f.readlines()
        for idx, line in enumerate(lines):
            parts = line.strip().split()
            if not parts:
                continue
            class_id = int(float(parts[0]))
            if class_id in target_classes:
                bbox_pool[class_id].append((label_file, idx))

# 🔄 Step 2: Randomly select which bounding boxes to keep
bbox_to_remove = defaultdict(set)  # {class_id: set of (file, line_index)}

for cls in target_classes:
    all_bboxes = bbox_pool[cls]
    print(f"Class {cls}: total {len(all_bboxes)} bounding boxes")
    if len(all_bboxes) <= max_instances:
        continue
    to_remove = random.sample(all_bboxes, len(all_bboxes) - max_instances)
    bbox_to_remove[cls] = set(to_remove)

# ✏️ Step 3: Rewrite label files with selected bboxes removed
removed_count = defaultdict(int)

for label_file in os.listdir(label_dir):
    if not label_file.endswith(".txt"):
        continue
    full_path = os.path.join(label_dir, label_file)
    with open(full_path, "r") as f:
        lines = f.readlines()

    new_lines = []
    for idx, line in enumerate(lines):
        parts = line.strip().split()
        if not parts:
            continue
        class_id = int(float(parts[0]))
        if (label_file, idx) in bbox_to_remove.get(class_id, set()):
            removed_count[class_id] += 1
            continue  # Skip this bounding box
        new_lines.append(line)

    # Write filtered lines back
    with open(full_path, "w") as f:
        f.writelines(new_lines)

print("✅ Done: Bounding boxes reduced.")
for cls in target_classes:
    print(f"Class {cls}: Removed {removed_count[cls]} excess bboxes")


Class 3: total 20000 bounding boxes
Class 7: total 13364 bounding boxes
Class 9: total 20383 bounding boxes
✅ Done: Bounding boxes reduced.
Class 3: Removed 8000 excess bboxes
Class 7: Removed 1364 excess bboxes
Class 9: Removed 8383 excess bboxes


In [16]:
from collections import Counter
from pathlib import Path

label_dirs = ['./data/test/labels', './data/train/labels', './data/valid/labels']  # Adjust if your structure is different
class_counter = Counter()

for label_dir in label_dirs:
    for label_file in Path(label_dir).rglob('*.txt'):
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if parts:  # skip empty lines
                    class_id = int(float(parts[0])) 
                    class_counter[class_id] += 1

print("📊 Final Class Distribution:")
for cls_id in sorted(class_counter):
    print(f"Class {cls_id}: {class_counter[cls_id]} instances")

📊 Final Class Distribution:
Class 0: 8850 instances
Class 1: 10667 instances
Class 2: 11404 instances
Class 3: 26641 instances
Class 4: 5880 instances
Class 5: 8720 instances
Class 6: 8116 instances
Class 7: 17787 instances
Class 8: 6958 instances
Class 9: 20299 instances


In [15]:
import os
import random
from collections import defaultdict

# 📁 Paths
label_dir = "./data/train/labels"

# ⚙️ Config
target_classes = [3, 7, 9]
max_instances = 12000

# 🧠 Step 1: Collect all lines per class (class → [(file, line_content)])
bbox_pool = defaultdict(list)

for label_file in os.listdir(label_dir):
    if not label_file.endswith(".txt"):
        continue
    full_path = os.path.join(label_dir, label_file)
    with open(full_path, "r") as f:
        lines = f.readlines()
        for line in lines:
            line = line.strip()
            if not line:
                continue
            class_id = int(float(line.split()[0]))
            if class_id in target_classes:
                bbox_pool[class_id].append((label_file, line))

# 🧮 Step 2: Decide which bboxes to remove
remove_lines = defaultdict(lambda: defaultdict(set))  # {file: {line_content}}

for cls in target_classes:
    bboxes = bbox_pool[cls]
    print(f"Class {cls}: {len(bboxes)} total bboxes")
    if len(bboxes) <= max_instances:
        continue
    to_remove = random.sample(bboxes, len(bboxes) - max_instances)
    for label_file, line_content in to_remove:
        remove_lines[label_file][line_content] = True

# ✏️ Step 3: Rewrite label files with unwanted bboxes removed
removed_count = defaultdict(int)

for label_file in os.listdir(label_dir):
    if not label_file.endswith(".txt"):
        continue

    full_path = os.path.join(label_dir, label_file)
    with open(full_path, "r") as f:
        lines = f.readlines()

    new_lines = []
    for line in lines:
        clean_line = line.strip()
        if clean_line in remove_lines[label_file]:
            class_id = int(float(clean_line.split()[0]))
            removed_count[class_id] += 1
            continue
        new_lines.append(line)

    with open(full_path, "w") as f:
        f.writelines(new_lines)

print("✅ Done. Final removals:")
for cls in target_classes:
    print(f"Class {cls}: Removed {removed_count[cls]} bboxes")


Class 3: 12000 total bboxes
Class 7: 12000 total bboxes
Class 9: 12000 total bboxes
✅ Done. Final removals:
Class 3: Removed 0 bboxes
Class 7: Removed 0 bboxes
Class 9: Removed 0 bboxes


In [18]:
import os
from collections import defaultdict

label_dir = "./data/train/labels"
target_classes = [3, 7, 9]
max_per_class = 12000

# Count how many of each class we keep
class_counts = defaultdict(int)

for filename in os.listdir(label_dir):
    if not filename.endswith(".txt"):
        continue

    file_path = os.path.join(label_dir, filename)

    with open(file_path, 'r') as f:
        lines = f.readlines()

    new_lines = []
    for line in lines:
        parts = line.strip().split()
        if not parts:
            continue

        try:
            class_id = int(float(parts[0]))
        except ValueError:
            continue  # Skip bad lines

        if class_id in target_classes:
            if class_counts[class_id] < max_per_class:
                new_lines.append(line)
                class_counts[class_id] += 1
            else:
                continue  # Skip this bbox
        else:
            new_lines.append(line)  # Keep all other class bboxes

    # Overwrite the file with filtered bboxes
    with open(file_path, 'w') as f:
        f.writelines(new_lines)

# ✅ Summary
print("✅ Done reducing high-frequency bounding boxes:")
for cls in target_classes:
    print(f"Class {cls}: {class_counts[cls]} bboxes kept (target: {max_per_class})")


✅ Done reducing high-frequency bounding boxes:
Class 3: 12000 bboxes kept (target: 12000)
Class 7: 12000 bboxes kept (target: 12000)
Class 9: 12000 bboxes kept (target: 12000)


In [25]:
from collections import Counter
from pathlib import Path

label_dirs = ['./data/test/labels', './data/train/labels', './data/valid/labels']  # Adjust if your structure is different
class_counter = Counter()

for label_dir in label_dirs:
    for label_file in Path(label_dir).rglob('*.txt'):
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if parts:  # skip empty lines
                    class_id = int(float(parts[0])) 
                    class_counter[class_id] += 1

print("📊 Final Class Distribution:")
for cls_id in sorted(class_counter):
    print(f"Class {cls_id}: {class_counter[cls_id]} instances")

📊 Final Class Distribution:
Class 0: 8850 instances
Class 1: 10667 instances
Class 2: 11404 instances
Class 3: 26641 instances
Class 4: 5880 instances
Class 5: 8720 instances
Class 6: 8116 instances
Class 7: 17787 instances
Class 8: 6958 instances
Class 9: 20299 instances


In [20]:
import os
from collections import defaultdict

label_dir = "./data/train/labels"
target_classes = [3, 7, 9]
max_per_class = 12000

# Count how many of each class we keep
class_counts = defaultdict(int)

for filename in os.listdir(label_dir):
    if not filename.endswith(".txt"):
        continue

    file_path = os.path.join(label_dir, filename)

    with open(file_path, 'r') as f:
        lines = f.readlines()

    new_lines = []
    for line in lines:
        parts = line.strip().split()
        if not parts:
            continue

        try:
            class_id = int(float(parts[0]))
        except ValueError:
            continue  # Skip bad lines

        if class_id in target_classes:
            if class_counts[class_id] < max_per_class:
                new_lines.append(line)
                class_counts[class_id] += 1
            else:
                continue  # Skip this bbox
        else:
            new_lines.append(line)  # Keep all other class bboxes

    # Overwrite the file with filtered bboxes
    with open(file_path, 'w') as f:
        f.writelines(new_lines)

# ✅ Summary
print("✅ Done reducing high-frequency bounding boxes:")
for cls in target_classes:
    print(f"Class {cls}: {class_counts[cls]} bboxes kept (target: {max_per_class})")


✅ Done reducing high-frequency bounding boxes:
Class 3: 12000 bboxes kept (target: 12000)
Class 7: 12000 bboxes kept (target: 12000)
Class 9: 12000 bboxes kept (target: 12000)


In [32]:
import os
import random
from collections import defaultdict

# Your target limits for the overrepresented classes
target_per_class = {
    3: 12000,
    7: 12000,
    9: 12000,
}

# Path to your existing train folder
train_dir = "./data/train/labels"  # adjust if needed

# Count current instances per class
bbox_count = defaultdict(int)
file_bboxes = defaultdict(list)  # filename → list of (class_id, line)

# Step 1: Read all labels and count bboxes per class
for file in os.listdir(train_dir):
    if not file.endswith(".txt"):
        continue
    path = os.path.join(train_dir, file)
    with open(path, "r") as f:
        lines = f.readlines()
        for idx, line in enumerate(lines):
            parts = line.strip().split()
            if len(parts) < 5:
                continue  # skip bad format
            cls_id = int(float(parts[0]))
            bbox_count[cls_id] += 1
            file_bboxes[file].append((cls_id, line))

# Step 2: Shuffle all bboxes for target classes
removal_plan = defaultdict(list)  # class_id → list of (file, line)

for file, items in file_bboxes.items():
    for cls_id, line in items:
        if cls_id in target_per_class:
            removal_plan[cls_id].append((file, line))

# Shuffle and keep only needed number
to_keep = {k: target_per_class[k] for k in target_per_class}
to_remove = {}

for cls_id, entries in removal_plan.items():
    random.shuffle(entries)
    to_keep_count = target_per_class[cls_id]
    to_remove[cls_id] = entries[to_keep_count:]  # everything after N entries

# Step 3: Edit files and remove excess bboxes
file_lines_map = {}  # Cache file → lines to write

for cls_id, items in to_remove.items():
    for file, line in items:
        if file not in file_lines_map:
            path = os.path.join(train_dir, file)
            with open(path, "r") as f:
                file_lines_map[file] = f.readlines()
        try:
            file_lines_map[file].remove(line)
        except ValueError:
            continue  # already removed or mismatch

# Step 4: Overwrite edited files
for file, lines in file_lines_map.items():
    with open(os.path.join(train_dir, file), "w") as f:
        f.writelines(lines)

# Step 5: Print final stats
final_count = defaultdict(int)
for file in os.listdir(train_dir):
    if not file.endswith(".txt"):
        continue
    with open(os.path.join(train_dir, file)) as f:
        for line in f:
            parts = line.strip().split()
            if parts:
                cls_id = int(float(parts[0]))
                final_count[cls_id] += 1

print("✅ Final Class Distribution:")
for cls_id in sorted(final_count.keys()):
    print(f"Class {cls_id}: {final_count[cls_id]} instances")


✅ Final Class Distribution:
Class 0: 6941 instances
Class 1: 7432 instances
Class 2: 7898 instances
Class 3: 12000 instances
Class 4: 4771 instances
Class 5: 5996 instances
Class 6: 6531 instances
Class 7: 12000 instances
Class 8: 5281 instances
Class 9: 12000 instances


In [33]:
from collections import Counter
from pathlib import Path

label_dirs = ['./data/test/labels', './data/train/labels', './data/valid/labels']  # Adjust if your structure is different
class_counter = Counter()

for label_dir in label_dirs:
    for label_file in Path(label_dir).rglob('*.txt'):
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if parts:  # skip empty lines
                    class_id = int(float(parts[0])) 
                    class_counter[class_id] += 1

print("📊 Final Class Distribution:")
for cls_id in sorted(class_counter):
    print(f"Class {cls_id}: {class_counter[cls_id]} instances")

📊 Final Class Distribution:
Class 0: 8850 instances
Class 1: 10667 instances
Class 2: 11404 instances
Class 3: 26641 instances
Class 4: 5880 instances
Class 5: 8720 instances
Class 6: 8116 instances
Class 7: 17787 instances
Class 8: 6958 instances
Class 9: 20299 instances


In [34]:
from pathlib import Path
from collections import defaultdict
import random

# Set maximum limit per class
TARGET_COUNT = 12000
class_limit = defaultdict(lambda: TARGET_COUNT)
class_counts = defaultdict(int)

# Label dirs
label_dirs = ['./data/train/labels', './data/valid/labels', './data/test/labels']

# First pass: Shuffle all label files
all_label_files = list(Path(dir).rglob('*.txt') for dir in label_dirs)
all_label_files = [file for sublist in all_label_files for file in sublist]
random.shuffle(all_label_files)

for label_file in all_label_files:
    with open(label_file, 'r') as f:
        lines = f.readlines()
    
    new_lines = []
    for line in lines:
        if line.strip():
            class_id = int(float(line.strip().split()[0]))
            if class_counts[class_id] < class_limit[class_id]:
                new_lines.append(line)
                class_counts[class_id] += 1

    # Overwrite the file with only kept lines
    with open(label_file, 'w') as f:
        f.writelines(new_lines)

print("✅ Final removals complete.")
for cid in sorted(class_counts):
    print(f"Class {cid}: {class_counts[cid]} kept")


✅ Final removals complete.
Class 0: 8850 kept
Class 1: 10667 kept
Class 2: 11404 kept
Class 3: 12000 kept
Class 4: 5880 kept
Class 5: 8720 kept
Class 6: 8116 kept
Class 7: 12000 kept
Class 8: 6958 kept
Class 9: 12000 kept


In [35]:
from collections import Counter
from pathlib import Path

label_dirs = ['./data/test/labels', './data/train/labels', './data/valid/labels']  # Adjust if your structure is different
class_counter = Counter()

for label_dir in label_dirs:
    for label_file in Path(label_dir).rglob('*.txt'):
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if parts:  # skip empty lines
                    class_id = int(float(parts[0])) 
                    class_counter[class_id] += 1

print("📊 Final Class Distribution:")
for cls_id in sorted(class_counter):
    print(f"Class {cls_id}: {class_counter[cls_id]} instances")

📊 Final Class Distribution:
Class 0: 8850 instances
Class 1: 10667 instances
Class 2: 11404 instances
Class 3: 12000 instances
Class 4: 5880 instances
Class 5: 8720 instances
Class 6: 8116 instances
Class 7: 12000 instances
Class 8: 6958 instances
Class 9: 12000 instances
